In [170]:
import pandas as pd
import csv

The table of toronto neighborhoods is available at https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M

This table has been converted into a pandas datframe below: 


In [171]:
df=pd.read_html('https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M')

In [172]:
print(df[0])

    Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                          Neighborhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       

In [173]:
df1=pd.DataFrame()

In [174]:
df1.insert(0,'Postal Code',df[0]['Postal Code'])
df1.insert(1,'Borough',df[0]['Borough'])
df1.insert(2,'Neighborhood',df[0]['Neighborhood'])

In [175]:
df1.reset_index()
df1

Postal Code           Borough  \
0           M1A      Not assigned   
1           M2A      Not assigned   
2           M3A        North York   
3           M4A        North York   
4           M5A  Downtown Toronto   
..          ...               ...   
175         M5Z      Not assigned   
176         M6Z      Not assigned   
177         M7Z      Not assigned   
178         M8Z         Etobicoke   
179         M9Z      Not assigned   

                                          Neighborhood  
0                                         Not assigned  
1                                         Not assigned  
2                                            Parkwoods  
3                                     Victoria Village  
4                            Regent Park, Harbourfront  
..                                                 ...  
175                                       Not assigned  
176                                       Not assigned  
177                                       Not assigned  
178  Mimico NW, The Queensway West, South of Bloor,...  
179                                       Not assigned  

[180 rows x 3 columns]

Dropping rows with Na values:

In [176]:
df1.drop(df1[df1.Borough=='Not assigned'].index,inplace=True)


In [251]:

df1=df1.drop('Unnamed: 0.1',axis=1)
df1.head(20)

KeyError: "['Unnamed: 0.1'] not found in axis"

In [180]:
df1.loc[df1['Neighborhood']=='Not assigned','Neighborhood']=df1.Borough

In [196]:
df1=df1.reset_index(drop=True)
df1=df1.drop(df1.index[11])# drop this row since foursquare returns no venues for this
df1=df1.reset_index(drop=True)
df1.head(20)

Postal Code           Borough  \
0          M3A        North York   
1          M4A        North York   
2          M5A  Downtown Toronto   
3          M6A        North York   
4          M7A  Downtown Toronto   
5          M9A         Etobicoke   
6          M1B       Scarborough   
7          M3B        North York   
8          M4B         East York   
9          M5B  Downtown Toronto   
10         M6B        North York   
11         M1C       Scarborough   
12         M3C        North York   
13         M4C         East York   
14         M5C  Downtown Toronto   
15         M6C              York   
16         M9C         Etobicoke   
17         M1E       Scarborough   
18         M4E      East Toronto   
19         M5E  Downtown Toronto   

                                         Neighborhood  
0                                           Parkwoods  
1                                    Victoria Village  
2                           Regent Park, Harbourfront  
3                    Lawrence Manor, Lawrence Heights  
4         Queen's Park, Ontario Provincial Government  
5             Islington Avenue, Humber Valley Village  
6                                      Malvern, Rouge  
7                                           Don Mills  
8                     Parkview Hill, Woodbine Gardens  
9                            Garden District, Ryerson  
10                                          Glencairn  
11             Rouge Hill, Port Union, Highland Creek  
12                                          Don Mills  
13                                   Woodbine Heights  
14                                     St. James Town  
15                                 Humewood-Cedarvale  
16  Eringate, Bloordale Gardens, Old Burnhamthorpe...  
17                  Guildwood, Morningside, West Hill  
18                                        The Beaches  
19                                        Berczy Park

In [199]:
df1.shape

(102, 3)

In [200]:
!conda install -c conda-forge geopy --yes

Solving environment: done

# All requested packages already installed.



import Nominatim to find coordinates of neighborhoods:

In [201]:
from geopy.geocoders import Nominatim

In [202]:
df1['latitude']=""
df1['longitude']=""


After Cleaning the data and dropping rows whose coordinates could not be find by using Nominatim Package, a csv file 'Toronto_areas' was created. Can be accesed below:-

In [203]:
df1=pd.read_csv('Toronto_areas.csv',header=0)


The code below finds the coordinates of the neighborhoods and adds them to the data frame. The process might take a few minutes.


In [204]:
for nd in df1['Neighborhood']:
    address=nd.split(',')[0]+",Toronto"
    geolocator = Nominatim(user_agent="toronto")
    location = geolocator.geocode(address)
    df1.loc[df1['Neighborhood'].str.contains(nd.split(',')[0]),'latitude']=location.latitude
    df1.loc[df1['Neighborhood'].str.contains(nd.split(',')[0]),'longitude']=location.longitude

In [205]:
df1=df1.drop('Unnamed: 0',axis=1)


In [206]:
df1.head()


Unnamed: 0.1 Postal Code           Borough  \
0             0         M3A        North York   
1             1         M4A        North York   
2             2         M5A  Downtown Toronto   
3             3         M6A        North York   
4             4         M7A  Downtown Toronto   

                                  Neighborhood   latitude  longitude  
0                                    Parkwoods  43.758800 -79.320197  
1                             Victoria Village  43.732658 -79.311189  
2                    Regent Park, Harbourfront  43.660706 -79.360457  
3             Lawrence Manor, Lawrence Heights  43.722079 -79.437507  
4  Queen's Park, Ontario Provincial Government  43.659659 -79.390340

In [207]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(df1['Borough'].unique()),
        df1.shape[0]
    )
)

The dataframe has 9 boroughs and 90 neighborhoods.


In [208]:
address = 'Toronto, Ontario'

geolocator = Nominatim(user_agent="-")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographical coordinates of Toronto are {}, {}.'.format(latitude, longitude))

The geographical coordinates of Toronto are 43.6534817, -79.3839347.


Visualisation of the slected neighborhood using folium:

In [209]:
!conda install -c conda-forge folium=0.5.0 --yes
import folium


Solving environment: done

# All requested packages already installed.



In [210]:
Toronto_map=folium.Map(location=[latitude,longitude],zoom_start=10)
for lat, lng, borough, neighborhood in zip(df1['latitude'], df1['longitude'], df1['Borough'],df1['Neighborhood']):
    label = '{},{}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.4,
        parse_html=False).add_to(Toronto_map)  
    
Toronto_map


Foursquare API has been used to get Venues Data. The API credentials are listed below.


In [211]:
import requests
from pandas.io.json import json_normalize 
CLIENT_ID = 'QXPPBDMPWTHSFATQGXNDG3SFDXEAR1K52Z1HF4BPMHCY4LDI' 
CLIENT_SECRET = 'UK0B3LTBOZD50XOUZSCEQCFXHUBCHDVJK5JCYUTAANEENHPO' 
#VERSION = '20180605' # Foursquare API version
VERSION = '20200101'
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: QXPPBDMPWTHSFATQGXNDG3SFDXEAR1K52Z1HF4BPMHCY4LDI
CLIENT_SECRET:UK0B3LTBOZD50XOUZSCEQCFXHUBCHDVJK5JCYUTAANEENHPO


In [212]:
radius=30000 #distance in metres around location (range)
Limit=500 #search results max
url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            latitude, 
            longitude, 
            radius, 
            Limit)
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5ee193d1b440000a49b0d877'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Toronto',
  'headerFullLocation': 'Toronto',
  'headerLocationGranularity': 'city',
  'totalResults': 241,
  'suggestedBounds': {'ne': {'lat': 43.92348197000027,
    'lng': -79.01145953565931},
   'sw': {'lat': 43.38348142999973, 'lng': -79.75640986434068}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '5227bb01498e17bf485e6202',
       'name': 'Downtown Toronto',
       'location': {'lat': 43.65323167517444,
        'lng': -79.38529600606677,
        'labeledLatLngs': [{'label': 'display',
          'lat': 43.65323167517444,
          'lng': -79.38529600606677}],
    

In [213]:
venues = results['response']['groups'][0]['items']
nearby_venues = json_normalize(venues) #convert the json response to a pandas DataFrame
nearby_venues.reset_index()

/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:2: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  


index                       referralId  reasons.count  \
0       0   e-0-5227bb01498e17bf485e6202-0              0   
1       1   e-0-4ad4c062f964a520b5f720e3-1              0   
2       2   e-0-55a9c018498e8b05f7f870f1-2              0   
3       3   e-0-4ad4c05ef964a520daf620e3-3              0   
4       4   e-0-5a81ae339deb7d369fa7f146-4              0   
..    ...                              ...            ...   
95     95  e-0-4bb75e0f6edc76b03212321c-95              0   
96     96  e-0-53b8466a498e83df908c3f21-96              0   
97     97  e-0-55637f1c498ecfe4c5dd2322-97              0   
98     98  e-0-4b9333f1f964a520fa3a34e3-98              0   
99     99  e-0-593b43e3e185f37c5a529082-99              0   

                                        reasons.items  \
0   [{'summary': 'This spot is popular', 'type': '...   
1   [{'summary': 'This spot is popular', 'type': '...   
2   [{'summary': 'This spot is popular', 'type': '...   
3   [{'summary': 'This spot is popular', 'type': '...   
4   [{'summary': 'This spot is popular', 'type': '...   
..                                                ...   
95  [{'summary': 'This spot is popular', 'type': '...   
96  [{'summary': 'This spot is popular', 'type': '...   
97  [{'summary': 'This spot is popular', 'type': '...   
98  [{'summary': 'This spot is popular', 'type': '...   
99  [{'summary': 'This spot is popular', 'type': '...   

                    venue.id                        venue.name  \
0   5227bb01498e17bf485e6202                  Downtown Toronto   
1   4ad4c062f964a520b5f720e3  Elgin And Winter Garden Theatres   
2   55a9c018498e8b05f7f870f1                               Alo   
3   4ad4c05ef964a520daf620e3            Art Gallery of Ontario   
4   5a81ae339deb7d369fa7f146                     Hailed Coffee   
..                       ...                               ...   
95  4bb75e0f6edc76b03212321c                     Serano Bakery   
96  53b8466a498e83df908c3f21                     Tandem Coffee   
97  55637f1c498ecfe4c5dd2322                     Boxcar Social   
98  4b9333f1f964a520fa3a34e3                   Coronation Park   
99  593b43e3e185f37c5a529082                  Tennessee Tavern   

    venue.location.lat  venue.location.lng  \
0            43.653232          -79.385296   
1            43.653394          -79.378507   
2            43.648574          -79.396243   
3            43.654003          -79.392922   
4            43.658833          -79.383684   
..                 ...                 ...   
95           43.683139          -79.346531   
96           43.653559          -79.361809   
97           43.659723          -79.346871   
98           43.634553          -79.405403   
99           43.639971          -79.439874   

                        venue.location.labeledLatLngs  \
0   [{'label': 'display', 'lat': 43.65323167517444...   
1   [{'label': 'display', 'lat': 43.65339379601958...   
2   [{'label': 'display', 'lat': 43.64857357946059...   
3   [{'label': 'display', 'lat': 43.65400286033738...   
4   [{'label': 'display', 'lat': 43.65883296982352...   
..                                                ...   
95  [{'label': 'display', 'lat': 43.68313941878674...   
96  [{'label': 'display', 'lat': 43.65355870959944...   
97  [{'label': 'display', 'lat': 43.65972274135156...   
98  [{'label': 'display', 'lat': 43.63455322391303...   
99  [{'label': 'display', 'lat': 43.63997128734775...   

    venue.location.distance  ... venue.location.country  \
0                       113  ...                 Canada   
1                       437  ...                 Canada   
2                      1131  ...                 Canada   
3                       726  ...                 Canada   
4                       596  ...                 Canada   
..                      ...  ...                    ...   
95                     4468  ...                 Canada   
96                     1782  ...                 Canada   
97                     3

cleaning the above DataFrame and extracting proper values from the json response:


In [214]:
newDf_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, newDf_columns]
nearby_venues['venue.categories'] = nearby_venues.apply(lambda x: x['venue.categories'][0]['name'], axis=1)


In [215]:
nearby_venues

venue.name             venue.categories  \
0                   Downtown Toronto                 Neighborhood   
1   Elgin And Winter Garden Theatres                      Theater   
2                                Alo            French Restaurant   
3             Art Gallery of Ontario                  Art Gallery   
4                      Hailed Coffee                  Coffee Shop   
..                               ...                          ...   
95                     Serano Bakery                       Bakery   
96                     Tandem Coffee                  Coffee Shop   
97                     Boxcar Social                         Café   
98                   Coronation Park                         Park   
99                  Tennessee Tavern  Eastern European Restaurant   

    venue.location.lat  venue.location.lng  
0            43.653232          -79.385296  
1            43.653394          -79.378507  
2            43.648574          -79.396243  
3            43.654003          -79.392922  
4            43.658833          -79.383684  
..                 ...                 ...  
95           43.683139          -79.346531  
96           43.653559          -79.361809  
97           43.659723          -79.346871  
98           43.634553          -79.405403  
99           43.639971          -79.439874  

[100 rows x 4 columns]

As you can see, only 100 venues were returned when you search the whole of Toronto.
To solve this, a function 'getNearbyVenues()' is made to loop through all the neighborhoods in the data frame and return venues:

In [216]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
    
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            Limit)
            
        results = requests.get(url).json()["response"]['groups'][0]['items']
        for v in results:
            venues_list.append([
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']])
    return venues_list

The function above returns a list of venues and their coordinates. A data frame can be made from the list. 
//Assign the list to toronto_venue:

In [217]:
toronto_venue = getNearbyVenues(names=df1['Neighborhood'],
                                   latitudes=df1['latitude'],
                                   longitudes=df1['longitude']
                                  )

In [218]:
print(toronto_venue)

[['Parkwoods', 43.7587999, -79.3201966, "Allwyn's Bakery", 43.75984035203157, -79.32471879917513, 'Caribbean Restaurant'], ['Parkwoods', 43.7587999, -79.3201966, 'LCBO', 43.75777384662435, -79.31425673330513, 'Liquor Store'], ['Parkwoods', 43.7587999, -79.3201966, 'Petro-Canada', 43.75795, -79.315187, 'Gas Station'], ['Parkwoods', 43.7587999, -79.3201966, 'Shoppers Drug Mart', 43.76085733239677, -79.32496051573521, 'Pharmacy'], ['Parkwoods', 43.7587999, -79.3201966, 'Pizza Pizza', 43.76023098701761, -79.32566642761229, 'Pizza Place'], ['Parkwoods', 43.7587999, -79.3201966, 'TD Canada Trust', 43.7575688, -79.3149756, 'Bank'], ['Parkwoods', 43.7587999, -79.3201966, 'Family Food Fair Convenience', 43.760619989690674, -79.32445934492416, 'Convenience Store'], ['Parkwoods', 43.7587999, -79.3201966, 'Parkwoods Coin Laundry', 43.76038596280906, -79.32489395141602, 'Laundry Service'], ['Parkwoods', 43.7587999, -79.3201966, 'Bus Stop: 95 & 24', 43.75808322061637, -79.31498558606371, 'Bus Line']

Make a data frame name 'nearby_venue' from the list:

In [219]:
nearby_venue=pd.DataFrame(toronto_venue, columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category'])

In [220]:
nearby_venue.shape


(2966, 7)

In [221]:
nearby_venue.head(10)

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Parkwoods                43.7588              -79.320197   
1    Parkwoods                43.7588              -79.320197   
2    Parkwoods                43.7588              -79.320197   
3    Parkwoods                43.7588              -79.320197   
4    Parkwoods                43.7588              -79.320197   
5    Parkwoods                43.7588              -79.320197   
6    Parkwoods                43.7588              -79.320197   
7    Parkwoods                43.7588              -79.320197   
8    Parkwoods                43.7588              -79.320197   
9    Parkwoods                43.7588              -79.320197   

                          Venue  Venue Latitude  Venue Longitude  \
0               Allwyn's Bakery       43.759840       -79.324719   
1                          LCBO       43.757774       -79.314257   
2                  Petro-Canada       43.757950       -79.315187   
3            Shoppers Drug Mart       43.760857       -79.324961   
4                   Pizza Pizza       43.760231       -79.325666   
5               TD Canada Trust       43.757569       -79.314976   
6  Family Food Fair Convenience       43.760620       -79.324459   
7        Parkwoods Coin Laundry       43.760386       -79.324894   
8             Bus Stop: 95 & 24       43.758083       -79.314986   
9      Parkwoods Village Centre       43.760735       -79.324873   

         Venue Category  
0  Caribbean Restaurant  
1          Liquor Store  
2           Gas Station  
3              Pharmacy  
4           Pizza Place  
5                  Bank  
6     Convenience Store  
7       Laundry Service  
8              Bus Line  
9         Shopping Mall

In [222]:
map_of_venues = folium.Map(location=[latitude, longitude], zoom_start=11)

for lat, lng, label in zip(nearby_venue['Venue Latitude'], nearby_venue['Venue Longitude'], nearby_venue['Venue']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_of_venues)  
    
map_of_venues

As is evident from the map, most venues in the city are concentrated in and around Downtown Toronto and along Bloor Street. 

Neighborhoods grouped by venues below:


In [223]:
venues_grouped_by_neighborhood=nearby_venue.groupby('Neighborhood').count()

venues_grouped_by_neighborhood

Neighborhood Latitude  \
Neighborhood                                                             
Agincourt                                                           13   
Bathurst Manor, Wilson Heights, Downsview North                      8   
Bayview Village                                                     14   
Bedford Park, Lawrence Manor East                                    2   
Berczy Park                                                        100   
...                                                                ...   
Willowdale, Willowdale West                                         51   
Woburn                                                              25   
Woodbine Heights                                                     7   
York Mills West                                                     21   
York Mills, Silver Hills                                            21   

                                                 Neighborhood Longitude  \
Neighborhood                                                              
Agincourt                                                            13   
Bathurst Manor, Wilson Heights, Downsview North                       8   
Bayview Village                                                      14   
Bedford Park, Lawrence Manor East                                     2   
Berczy Park                                                         100   
...                                                                 ...   
Willowdale, Willowdale West                                          51   
Woburn                                                               25   
Woodbine Heights                                                      7   
York Mills West                                                      21   
York Mills, Silver Hills                                             21   

                                                 Venue  Venue Latitude  \
Neighborhood                                                             
Agincourt                                           13              13   
Bathurst Manor, Wilson Heights, Downsview North      8               8   
Bayview Village                                     14              14   
Bedford Park, Lawrence Manor East                    2               2   
Berczy Park                                        100             100   
...                                                ...             ...   
Willowdale, Willowdale West                         51              51   
Woburn                                              25              25   
Woodbine Heights                                     7               7   
York Mills West                                     21              21   
York Mills, Silver Hills                            21              21   

                                                 Venue Longitude  \
Neighborhood                                                       
Agincourt                                                     13   
Bathurst Manor, Wilson Heights, Downsview North                8   
Bayview Village                                               14   
Bedford Park, Lawrence Manor East                              2   
Berczy Park                                                  100   
...                                                          ...   
Willowdale, Willowdale West                                   51   
Woburn                                                        25   
Woodbine Heights                                               7   
York Mills West                                               21   
York Mills, Silver Hills                                      21   

                                                 Venue Category  
Neighborhood                                                     
Agincourt                                                    13  
Bathurst Manor, Wilson Heights, Downsview North               8 

In [224]:
print('There are {} uniques categories of venues in the city!!.'.format(len(nearby_venue['Venue Category'].unique())))

There are 276 uniques categories of venues in the city!!.


In [225]:
toronto_onehot = pd.get_dummies(nearby_venue[['Venue Category']],prefix="",prefix_sep="")
toronto_onehot['Neighborhood']=nearby_venue['Neighborhood']
toronto_onehot

Accessories Store  Afghan Restaurant  African Restaurant  \
0                     0                  0                   0   
1                     0                  0                   0   
2                     0                  0                   0   
3                     0                  0                   0   
4                     0                  0                   0   
...                 ...                ...                 ...   
2961                  0                  0                   0   
2962                  0                  0                   0   
2963                  0                  0                   0   
2964                  0                  0                   0   
2965                  0                  0                   0   

      American Restaurant  Animal Shelter  Antique Shop  Aquarium  \
0                       0               0             0         0   
1                       0               0             0         0   
2                       0               0             0         0   
3                       0               0             0         0   
4                       0               0             0         0   
...                   ...             ...           ...       ...   
2961                    0               0             0         0   
2962                    0               0             0         0   
2963                    0               0             0         0   
2964                    0               0             0         0   
2965                    0               0             0         0   

      Argentinian Restaurant  Art Gallery  Art Museum  ...  Video Game Store  \
0                          0            0           0  ...                 0   
1                          0            0           0  ...                 0   
2                          0            0           0  ...                 0   
3                          0            0           0  ...                 0   
4                          0            0           0  ...                 0   
...                      ...          ...         ...  ...               ...   
2961                       0            0           0  ...                 0   
2962                       0            0           0  ...                 0   
2963                       0            0           0  ...                 0   
2964                       0            0           0  ...                 0   
2965                       0            0           0  ...                 0   

      Video Store  Vietnamese Restaurant  Warehouse Store  Whisky Bar  \
0               0                      0                0           0   
1               0                      0                0           0   
2               0                      0                0           0   
3               0                      0                0           0   
4               0                      0                0           0   
...           ...                    ...              ...         ...   
2961            0                      0                0           0   
2962            0                      0                0           0   
2963            0                      0                0           0   
2964            0                      0                0           0   
2965            0                      0                0           0   

      Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  
0            0          0            0              0            0  
1            0          0            0              0            0  
2            0          0            0              0            0  
3            0          0            0              0            0  
4            0          0            0              0            0  
...        ...        ...          ...            ...          ...  
2961         0          0            0              0          

In [226]:
col_list = list(toronto_onehot.columns)
col_list.remove('Neighborhood')
cols = ['Neighborhood'] + [col for col in col_list]
toronto_onehot = toronto_onehot[cols]
toronto_onehot.head(50)

Neighborhood  Accessories Store  \
0                                     Parkwoods                  0   
1                                     Parkwoods                  0   
2                                     Parkwoods                  0   
3                                     Parkwoods                  0   
4                                     Parkwoods                  0   
5                                     Parkwoods                  0   
6                                     Parkwoods                  0   
7                                     Parkwoods                  0   
8                                     Parkwoods                  0   
9                                     Parkwoods                  0   
10                                    Parkwoods                  0   
11                                    Parkwoods                  0   
12                                    Parkwoods                  0   
13                                    Parkwoods                  0   
14                             Victoria Village                  0   
15                             Victoria Village                  0   
16                             Victoria Village                  0   
17                    Regent Park, Harbourfront                  0   
18                    Regent Park, Harbourfront                  0   
19                    Regent Park, Harbourfront                  0   
20                    Regent Park, Harbourfront                  0   
21                    Regent Park, Harbourfront                  0   
22                    Regent Park, Harbourfront                  0   
23                    Regent Park, Harbourfront                  0   
24                    Regent Park, Harbourfront                  0   
25                    Regent Park, Harbourfront                  0   
26                    Regent Park, Harbourfront                  0   
27                    Regent Park, Harbourfront                  0   
28                    Regent Park, Harbourfront                  0   
29                    Regent Park, Harbourfront                  0   
30                    Regent Park, Harbourfront                  0   
31                    Regent Park, Harbourfront                  0   
32                    Regent Park, Harbourfront                  0   
33                    Regent Park, Harbourfront                  0   
34                    Regent Park, Harbourfront                  0   
35                    Regent Park, Harbourfront                  0   
36                    Regent Park, Harbourfront                  0   
37                    Regent Park, Harbourfront                  0   
38                    Regent Park, Harbourfront                  0   
39             Lawrence Manor, Lawrence Heights                  0   
40             Lawrence Manor, Lawrence Heights                  0   
41             Lawrence Manor, Lawrence Heights                  0   
42             Lawrence Manor, Lawrence Heights                  0   
43             Lawrence Manor, Lawrence Heights                  0   
44  Queen's Park, Ontario Provincial Government                  0   
45  Queen's Park, Ontario Provincial Government                  0   
46  Queen's Park, Ontario Provincial Government                  0   
47  Queen's Park, Ontario Provincial Government                  0   
48  Queen's Park, Ontario Provincial Government                  0   
49  Queen's Park, Ontario Provincial Government                  0   

    Afghan Restaurant  African Restaurant  American Restaurant  \
0                   0                   0                    0   
1                   0                   0                    0   
2                   0                   0                    0   
3                   0                   0                    0   
4                   0                   0                    0   
5                   0                   0                    0   
6 

In [227]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Accessories Store  \
0                                         Agincourt                0.0   
1   Bathurst Manor, Wilson Heights, Downsview North                0.0   
2                                   Bayview Village                0.0   
3                 Bedford Park, Lawrence Manor East                0.0   
4                                       Berczy Park                0.0   
..                                              ...                ...   
80                      Willowdale, Willowdale West                0.0   
81                                           Woburn                0.0   
82                                 Woodbine Heights                0.0   
83                                  York Mills West                0.0   
84                         York Mills, Silver Hills                0.0   

    Afghan Restaurant  African Restaurant  American Restaurant  \
0                 0.0                 0.0                 0.00   
1                 0.0                 0.0                 0.00   
2                 0.0                 0.0                 0.00   
3                 0.0                 0.0                 0.00   
4                 0.0                 0.0                 0.01   
..                ...                 ...                  ...   
80                0.0                 0.0                 0.00   
81                0.0                 0.0                 0.00   
82                0.0                 0.0                 0.00   
83                0.0                 0.0                 0.00   
84                0.0                 0.0                 0.00   

    Animal Shelter  Antique Shop  Aquarium  Argentinian Restaurant  \
0              0.0          0.00       0.0                     0.0   
1              0.0          0.00       0.0                     0.0   
2              0.0          0.00       0.0                     0.0   
3              0.0          0.00       0.0                     0.0   
4              0.0          0.01       0.0                     0.0   
..             ...           ...       ...                     ...   
80             0.0          0.00       0.0                     0.0   
81             0.0          0.00       0.0                     0.0   
82             0.0          0.00       0.0                     0.0   
83             0.0          0.00       0.0                     0.0   
84             0.0          0.00       0.0                     0.0   

    Art Gallery  ...  Video Game Store  Video Store  Vietnamese Restaurant  \
0          0.00  ...              0.00          0.0               0.076923   
1          0.00  ...              0.00          0.0               0.000000   
2          0.00  ...              0.00          0.0               0.000000   
3          0.00  ...              0.00          0.0               0.000000   
4          0.02  ...              0.00          0.0               0.000000   
..          ...  ...               ...          ...                    ...   
80         0.00  ...              0.00          0.0               0.000000   
81         0.00  ...              0.04          0.0               0.040000   
82         0.00  ...              0.00          0.0               0.000000   
83         0.00  ...              0.00          0.0               0.000000   
84         0.00  ...              0.00          0.0               0.000000   

    Warehouse Store  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  \
0               0.0         0.0       0.0        0.0          0.0   
1               0.0         0.0       0.0        0.0          0.0   
2               0.0         0.0       0.0        0.0          0.0   
3               0.0         0.0       0.0        0.0          0.0   
4               0.0         0.0       0.0        0.0          0.0   
..              ...         ...       ...        ...          ...   
80              0.0         0.0       0.0        0.0          0.0   
81              0.0        

The most popular venues in each neighborhood:

In [228]:
for area in toronto_grouped['Neighborhood']:
    print("_____"+area+"_____")
    temp_df = toronto_grouped[toronto_grouped['Neighborhood'] == area].T.reset_index()
    temp_df.columns = ['venue','freq']
    temp_df = temp_df.iloc[1:] #to exclude index col
    temp_df['freq'] = temp_df['freq'].astype(float)
    temp_df = temp_df.round({'freq': 2})
    print(temp_df.sort_values('freq', ascending=False).reset_index(drop=True).head(5))
    print('\n\n')



_____Agincourt_____
                  venue  freq
0    Chinese Restaurant  0.15
1     Electronics Store  0.08
2  Cantonese Restaurant  0.08
3         Shopping Mall  0.08
4                Bakery  0.08



_____Bathurst Manor, Wilson Heights, Downsview North_____
                    venue  freq
0       French Restaurant  0.12
1                    Park  0.12
2           Metro Station  0.12
3  Furniture / Home Store  0.12
4             Bus Station  0.12



_____Bayview Village_____
                 venue  freq
0                 Bank  0.14
1       Clothing Store  0.07
2       Sandwich Place  0.07
3  Sporting Goods Shop  0.07
4       Breakfast Spot  0.07



_____Bedford Park, Lawrence Manor East_____
                        venue  freq
0  Construction & Landscaping   0.5
1         Rental Car Location   0.5
2           Accessories Store   0.0
3                 Music Store   0.0
4                      Office   0.0



_____Berczy Park_____
                 venue  freq
0          Coffee Shop  0.0

                  venue  freq
0           Pizza Place  0.17
1              Pharmacy  0.17
2  Fast Food Restaurant  0.17
3       Bubble Tea Shop  0.08
4                  Park  0.08



_____Milliken, Agincourt North, Steeles East, L'Amoreaux East_____
                 venue  freq
0  Japanese Restaurant  0.13
1   Chinese Restaurant  0.13
2     Asian Restaurant  0.08
3               Bakery  0.08
4          Gas Station  0.03



_____Mimico NW, The Queensway West, South of Bloor, Kingsway Park South West, Royal York South West_____
          venue  freq
0   Yoga Studio   0.2
1    Playground   0.2
2  Skating Rink   0.2
3        Bakery   0.2
4           Bar   0.2



_____Moore Park, Summerhill East_____
               venue  freq
0  Convenience Store   0.2
1                Gym   0.2
2               Park   0.2
3         Restaurant   0.2
4             Lawyer   0.2



_____New Toronto, Mimico South, Humber Bay Shores_____
                 venue  freq
0                 Café  0.10
1   Italian Resta

Making a dataframe with the top 10 venues in each neighborhood:

In [229]:
import numpy as np


ordinals = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(10):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1,ordinals[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']


        
for ind in np.arange(toronto_grouped.shape[0]):
    row=toronto_grouped.iloc[ind, :]
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    neighborhoods_venues_sorted.iloc[ind, 1:] = row_categories_sorted.index.values[0:10]

neighborhoods_venues_sorted.head(13)

Neighborhood  \
0                                           Agincourt   
1     Bathurst Manor, Wilson Heights, Downsview North   
2                                     Bayview Village   
3                   Bedford Park, Lawrence Manor East   
4                                         Berczy Park   
5        Brockton, Parkdale Village, Exhibition Place   
6   CN Tower, King and Spadina, Railway Lands, Har...   
7                                           Cedarbrae   
8                                  Central Bay Street   
9                                            Christie   
10                               Church and Wellesley   
11            Clarks Corners, Tam O'Shanter, Sullivan   
12    Cliffside, Cliffcrest, Scarborough Village West   

         1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Chinese Restaurant            Food Court  Hong Kong Restaurant   
1                Metro Station     French Restaurant           Gas Station   
2                         Bank   Sporting Goods Shop  Outdoor Supply Store   
3   Construction & Landscaping   Rental Car Location           Flower Shop   
4                  Coffee Shop                  Café            Restaurant   
5           Tibetan Restaurant           Pizza Place     Indian Restaurant   
6                        Hotel           Coffee Shop                   Bar   
7         Fast Food Restaurant           Coffee Shop          Optical Shop   
8                  Coffee Shop        Clothing Store                 Hotel   
9            Korean Restaurant           Coffee Shop        Ice Cream Shop   
10                 Coffee Shop      Sushi Restaurant   Japanese Restaurant   
11           Convenience Store           Gas Station  Caribbean Restaurant   
12                 Pizza Place              Pharmacy        Breakfast Spot   

   4th Most Common Venue 5th Most Common Venue   6th Most Common Venue  \
0      Korean Restaurant                Bakery   Vietnamese Restaurant   
1   Gym / Fitness Center           Coffee Shop  Furniture / Home Store   
2            Pizza Place        Breakfast Spot            Burger Joint   
3            Fish Market     Fish & Chips Shop     Filipino Restaurant   
4    Japanese Restaurant    Italian Restaurant            Cocktail Bar   
5                   Café                Bakery                   Diner   
6                    Gym           Pizza Place          Ice Cream Shop   
7          Shopping Mall          Liquor Store          Sandwich Place   
8                   Café                 Diner                   Plaza   
9           Dessert Shop          Cocktail Bar           Grocery Store   
10            Restaurant                  Café                 Gay Bar   
11           Fish Market     Fish & Chips Shop     Filipino Restaurant   
12        Sandwich Place                   Pub             Snack Place   

   7th Most Common Venue      8th Most Common Venue   9th Most Common Venue  \
0   Cantonese Restaurant          Electronics Store           Shopping Mall   
1                   Park                Bus Station      Falafel Restaurant   
2   Fast Food Restaurant                Gas Station          Sandwich Place   
3   Fast Food Restaurant             Farmers Market        Doner Restaurant   
4                 Bakery                   Beer Bar                   Hotel   
5             Restaurant                   Pharmacy    Caribbean Restaurant   
6               Aquarium             Scenic Lookout        Baseball Stadium   
7          Big Box Store                 Beer Store  Furniture / Home Store   
8         Cosmetics Shop  Middle Eastern Restaurant          Sandwich Place   
9                   Café                Karaoke Bar      Mexican Restaurant   
10           Yoga Studio                      Hotel            Dance Studio   
11  Fast Food Restaurant             Farmers Market              Donut Shop   
12         Grocery Store                Coffee Shop       Elementary School   

   10

In [230]:
from sklearn.cluster import KMeans
kclusters = 5 #randomly selected cluster numbers for now

toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# checking cluster labels 
kmeans.labels_

array([1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 3,
       1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 4, 1, 1, 4, 1,
       1, 1, 1, 1, 1, 1, 1, 2, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1],
      dtype=int32)

In [244]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
neighborhoods_venues_sorted.head(50)

ValueError: cannot insert Cluster Labels, already exists

Joining dataframes to create one final dataFrame 'toronto'

In [255]:
toronto=df1
toronto=toronto.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')
#toronto.drop('Unnamed: 0.1',axis=1)
toronto.head(50)
toronto=toronto.drop(toronto.index[11])


In [243]:
import matplotlib.cm as cm
import matplotlib.colors as colors

In [256]:
# create map


map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]



markers_colors = []
for lat, lon, poi, cluster in zip(toronto['latitude'], toronto['longitude'], toronto['Neighborhood'], toronto['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters